## Computation of homology groups with R, Q or Z/pZ coefficients

Suppose we are given an abstract simplicial complex $K$ as a set of its maximal simplices. Our task will be to determine the homology groups $H_*(|K|; F)$ of $|K|$ with coefficients in a field $F$, where $F$ is $\mathbb{R}$ or $\mathbb{Z}/p\mathbb{Z}$ for a prime $p$.

### Basic data manipulation

Our (abstract) simplicial complex $K$ will be given as a set/list of its maximal simplices, e.g. `K = [(1, 2, 3), (1, 2, 4), (2, 5)]`, So we will present each simplex as a tuple (e.g. $\tau = (1, 2, 3)$). To build a full simplicial complex, we will need all subtuples $\sigma \subseteq \tau$ of such tuples. As we already did once, we will present the full simplicial complex as a 'dimension dictionary', i.e., each `key => value` pair is of the form $d$ `=>` list of simplices of dimensions $d$ in $K$.

In [131]:
# Compute the boundary of a simplex sx and represent it as a list of maximal simplices, 
# i.e., just determine the codimension 1 faces of sx. 

# E.g. for sx = (1, 2, 3) we get [(1, 2), (1, 3), (2, 3)].

function simplex_boundary(sx)
    # determine the codimension 1 simplices in the boundary of the simplex sx
    # 'remove' one entry of a tuple at each specific index by splicing the corresponding subtuples
    cd1faces = ([(sx[1:k-1]..., sx[k+1:end]...) for k in eachindex(sx)])
    return cd1faces
end



# Create a dictionary of all simplices grouped by dimension for a simplicial complex
# represented by its maximal simplices.

function dim_dict_scx(max_scx)
    # determine the dimension+1 of the complex
    n = maximum([length(sx) for sx in max_scx])
    # set up the dictionary (empty vectors of k-tuples in each dimension)
    dimension_dict = Dict((k-1) => Vector{NTuple{k, Int}}() for k in 1:n)
    # add all simplices in max_scx to the dictionary
    # (Sorting of vertices is necessary for some direct comparisons in a later function...)
    for sx in max_scx
        push!(dimension_dict[length(sx)-1], Tuple(sort(collect(sx))))
    end
    # fill the dictionary with all simplices from top down
    for k in (n-1):-1:1
        for sx in dimension_dict[k]
            union!(dimension_dict[k-1], [Tuple(sort(collect(x))) for x in simplex_boundary(sx)])
        end
    end
    return dimension_dict
end

K = [(1, 2, 3), (1, 2, 4), (2, 5)]
dim_dict_scx(K)

Dict{Int64, Vector} with 3 entries:
  0 => [(5,), (2,), (3,), (1,), (4,)]
  2 => [(1, 2, 3), (1, 2, 4)]
  1 => [(2, 5), (2, 3), (1, 3), (1, 2), (2, 4), (1, 4)]

### Building the boundary matrix Dn

We will represent the boundary operator $\partial_n \colon C_n \to C_{n-1}$ with a matrix $D_n$ w.r.t. to the bases of $C_n$ and $C_{n-1}$ given in the above representation of $K$ (i.e., the simplices of appropriate dimensions form the corresponding bases).

In [132]:
# This function returns the n-th boundary matrix Dn with coefficients Z/pZ or R of a simplicial complex given as a dimension_dict.
# (p should be a prime. For convenience, p = 0 means R.)

# Do not forget to install the Primes package with
# using Pkg; Pkg.add("Primes")

using Primes
using Mods

function boundary_matrix(dimension_dict, n, p)
    # check if p is 0 or prime
    if p != 0 && !isprime(p)
        throw(DomainError(p, "p should be 0 or a prime."))
    end
    
    # cases n = 0 and n = dim+1 should be treated separately
    if n == 0
        Dn = zeros(p==0 ? Float64 : Mod{p}, 1, length(dimension_dict[n]))
    elseif n == maximum(keys(dimension_dict))+1
        Dn = zeros(p==0 ? Float64 : Mod{p}, length(dimension_dict[n-1]), 1)
    else
        Dn = zeros(p==0 ? Float64 : Mod{p}, length(dimension_dict[n-1]), length(dimension_dict[n]))
        # otherwise, just replace the zeroes with 1's or -1's at appropriate places
        domain = dimension_dict[n]
        codomain = dimension_dict[n-1]
        for j in eachindex(domain)
            # ===============
            # YOUR CODE HERE

            # ===============
        end
    end
    return Dn
end

boundary_matrix (generic function with 2 methods)

In [169]:
# Test it out.

Kmax = [(1, 2, 3), (1, 2, 4), (2, 5)]
K = dim_dict_scx(Kmax)

# choose p
p = 0

D2 = boundary_matrix(K, 2, p)
#D1 = boundary_matrix(K, 1, p)
#D0 = boundary_matrix(K, 0, p)


6×2 Matrix{Float64}:
  0.0   0.0
  1.0   0.0
 -1.0   0.0
  1.0   1.0
  0.0   1.0
  0.0  -1.0

In [170]:
# using LinearAlgebra

# determine the mod p Betti numbers of a simplicial complex given via its maximal simplices

function betti_numbers(max_scx, p = 0)

    # build the 'dimension dictionary' of a simplicial complex given via its maximal simplices
    dimension_dict = dim_dict_scx(max_scx)
    
    # determine the dimension of max_scx
    d = maximum(keys(dimension_dict))
    
    # initialize the vector of Betti numbers
    betti = []
    
    # the current (first) boundary matrix
    Dk1 = boundary_matrix(dimension_dict, 0, p)
    
    # determine the Betti numbers from two consecutive boundary matrices
    for k in 1:(d+1)
        
        # the next boundary matrix
        Dk = boundary_matrix(dimension_dict, k, p)

        # optional: if p = 0
        # use LinearAlgebra to compute ranks of Dk1 and Dk
        # and get the betti number from there
        # n_rows, n_cols = size(Dk1)
        # push!(betti, n_cols - rank(Dk1) - rank(Dk))
        
        # perform simultaneous reduction on D_{k-1} and D_k 
        # and store the corresponding Betti number

        push!(betti, simultaneous_reduce(Dk1, Dk))
         
        # use Dk as the current (first) boundary matrix
        Dk1 = Dk
    end
    return betti
end


# test it
betti_numbers(Kmax)

3-element Vector{Any}:
 1
 0
 0

In [166]:
function simultaneous_reduce(A, B)
    
    # throw a 'wrong size' error
    if size(A)[2] != size(B)[1]
        throw(DimensionMismatch("cols(A) != rows(B)"))
    end
    
    # store the number of rows and columns of A 
    n_rows, n_cols = size(A)
    
    # perform a column reduction on A and do the inverse operations on rows of B
    i, j = 1, 1
    last_nonzero_col = 0
    while i <= n_rows && j <= n_cols
        # check if A[i, j] can be used as a column pivot ...
        if A[i, j] == 0
            # if not, find a column pivot in the current row
            nonzero_col = j+1
            while nonzero_col <= n_cols && A[i, nonzero_col] == 0
                nonzero_col += 1;
            end
            # if there are only zeros in the current row to the right
            if nonzero_col == n_cols+1
                # go to a new row
                i += 1
                continue
            end
            
            # otherwise swap the columns of A ...
            # ===============
            # YOUR CODE HERE

            # ===============
            
            # ... and corresponding rows of B
            # ===============
            # YOUR CODE HERE

            # ===============
        end
        # store last nonzero column (for additional row reduction on B later)
        last_nonzero_col = j
        
        # ... and set A[i, j] as the new column pivot entry 
        # ===============
        # YOUR CODE HERE

        # ===============
        
        # set that column pivot to 1 (in A)
        # and do the inverse operation on B
        # ===============
        # YOUR CODE HERE

        # ===============
        
        # annihilate the nonzero elements to the right of the pivot in A
        # and do the opposite transformations on B
        # ===============
        # YOUR CODE HERE

        # ===============
        
        # increase row and column indices and search for the next pivot
        i += 1
        j += 1
    end
    
    # now perform a row reduction on nonzero rows of B 
    # (Performing inverse operations on columns of A would only be required to keep track of the generators...)
    n_rows, n_cols = size(B)
    i, j = last_nonzero_col+1, 1
    last_nonzero_row = last_nonzero_col
    while i <= n_rows && j <= n_cols
        # check if B[i, j] can be used as a column pivot ...
        if B[i, j] == 0
            # if not, find a row pivot in the current column
            nonzero_row = i+1
            while nonzero_row <= n_rows && B[nonzero_row, j] == 0
                nonzero_row += 1
            end
            # if there are only zeros in the current column downwards
            if nonzero_row == n_rows+1
                # go to a new column
                j += 1
                continue
            end
            # otherwise swap the rows of B
            # (The corresponding columns of the column-reduced A are 0, no need to swap those...)
            # ===============
            # YOUR CODE HERE

            # ===============
            
        end
        
        # store last nonzero row (to return the 'Betti number')
        last_nonzero_row = i
        
        # Set B[i, j] as the new pivot entry ...
        # ===============
        # YOUR CODE HERE

        # ===============
        
        # ... and set that pivot to 1.
        # ===============
        # YOUR CODE HERE

        # ===============
        
        # annihilate the nonzero elements below the pivot in B
        # (No need for inverse operations on the columns of the reduced A...)
        # ===============
        # YOUR CODE HERE

        # ===============
        
        # increase row and column indices and search for the next pivot
        i += 1
        j += 1
    end
    
    # return the corresponding Betti number
    return n_rows - last_nonzero_row
end

simultaneous_reduce (generic function with 1 method)

## Some use examples

Given abstract simplicial complexes below (via their maximal simplices) determine their Betti numbers (mod $p$).

In [167]:
A = [(1, 2, 3), (1, 2, 4), (1, 3, 4), (2, 3, 4)];
B = [(1, 2, 3), (1, 2, 4), (2, 3, 5), (2, 3, 6), (3, 5, 7)];
C = [(1, 2, 3), (2, 3, 4), (3, 4, 5), (4, 5, 6), (1, 5, 6), (1, 2, 6)];
D = [(1, 2, 4), (2, 4, 6), (2, 3, 6), (3, 6, 8), (1, 3, 8), (1, 4, 8), (4, 5, 6), (5, 6, 7), (6, 7, 8), (7, 8, 9), (4, 8, 9), (4, 5, 9), (1, 5, 7), (1, 2, 7), (2, 7, 9), (2, 3, 9), (3, 5, 9), (1, 3, 5)];
E = [(1, 2, 4), (2, 4, 6), (2, 3, 6), (3, 6, 8), (1, 3, 8), (1, 5, 8), (4, 5, 6), (5, 6, 7), (6, 7, 8), (7, 8, 9), (5, 8, 9), (4, 5, 9), (1, 5, 7), (1, 2, 7), (2, 7, 9), (2, 3, 9), (3, 4, 9), (1, 3, 4)];
F = [(1, 2, 3), (1, 3, 4), (2, 3, 4), (4, 5, 6)];
G = [(1, 2, 3), (2, 3, 4), (3, 4, 5), (4, 5, 6), (2, 5, 6), (1, 2, 6)];
H = [(1, 3, 5), (1, 2, 6), (1, 5, 6), (1, 2, 4), (1, 3, 4), (2, 3, 5), (2, 3, 6), (2, 4, 5), (3, 4, 6), (4, 5, 6)];
RP2 = [(1, 2, 7), (1, 3, 7), (2, 5, 7), (3, 6, 7), (2, 3, 5), (3, 4, 5), (4, 5, 7), (4, 6, 7), (2, 4, 6), (2, 3, 6), (1, 3, 4), (1, 2, 4)];
RP2_ = [(1, 3, 4), (1, 4, 5), (1, 2, 5), (2, 3, 4), (2, 4, 6), (4, 5, 6), (3, 6, 5), (2, 3, 5), (1, 2, 6), (1, 3, 6)];

In [171]:
# test it
betti_numbers(A, 0)

3-element Vector{Any}:
 1
 0
 1